# Hetzner VPS Setup Guide - Complete Instructions

## Session 6: Live Trading & Deployment

**Today's Objectives:**
- Secure API key management & best practices
- Choose the right deployment platform
- Set up automated execution on Hetzner Cloud

## Step 1: Create Account & Choose Server

### 1.1 Create Hetzner Account
1. Go to [hetzner.com](https://www.hetzner.com/)
2. Click "Sign Up" and create your account
3. Verify your email address
4. Add payment method (credit card or PayPal)

### 1.2 Create Your Server
1. Log into Hetzner Cloud Console
2. Click "New Project" → Name it "crypto-trading-bot"
3. Click "Add Server"
4. **Choose Location**: Nuremberg or Helsinki (closest to major EU exchanges)
5. **Choose Image**: Ubuntu 22.04
6. **Choose Type**: CX11 (1 vCPU, 2GB RAM, 20GB storage) - €3.29/month
7. **SSH Key Setup**:
   - If you have SSH key: Upload your public key
   - If you don't: Select "Password" (we'll create SSH key later)
8. **Server Name**: "trading-bot-server"
9. Click "Create & Buy Now"

**Your server will be ready in 30-60 seconds!**

## Step 2: Ubuntu Setup & SSH Access

### 2.1 For Linux/Mac Users

Replace `YOUR_SERVER_IP` with your actual server IP from Hetzner console:

In [ ]:
# Connect to your server (run in terminal, not Jupyter)
# If you used SSH key during setup:
ssh root@YOUR_SERVER_IP

# If you used password:
ssh root@YOUR_SERVER_IP
# Enter the password from Hetzner console

#### Create SSH Key (if you didn't have one)

In [ ]:
# On your local machine (run in terminal, not Jupyter):
ssh-keygen -t rsa -b 4096 -C "your-email@example.com"
# Press Enter for default location
# Press Enter for no passphrase (or set one if you prefer)

# Copy your public key to server:
ssh-copy-id root@YOUR_SERVER_IP

### 2.2 For Windows Users

#### Option A: Use Windows Terminal (Recommended)
1. Install Windows Terminal from Microsoft Store
2. Open Terminal and use same commands as Linux/Mac above

#### Option B: Use PuTTY
1. Download PuTTY from [putty.org](https://www.putty.org/)
2. Open PuTTY
3. **Host Name**: YOUR_SERVER_IP
4. **Port**: 22
5. **Connection Type**: SSH
6. Click "Open"
7. Username: `root`
8. Password: (from Hetzner console)

In [ ]:
# Create SSH Key for Windows (run in Windows Terminal or PowerShell):
ssh-keygen -t rsa -b 4096 -C "your-email@example.com"
# Keys will be saved in C:\Users\YourName\.ssh\

## Step 3: Install Python & Dependencies

**⚠️ Important: The following commands should be run on your Hetzner server (via SSH), not in this Jupyter notebook!**

### 3.1 Update System

In [ ]:
# Update package list and upgrade system
sudo apt update && sudo apt upgrade -y

### 3.2 Install Python and Pip

In [ ]:
# Install Python 3 and pip
sudo apt install python3 python3-pip python3-venv -y

# Check installation
python3 --version
pip3 --version

### 3.3 Install Required Python Libraries

In [ ]:
# Install common trading libraries
pip3 install pandas numpy ccxt python-dotenv requests

# For backtesting (if using backtesting.py)
pip3 install backtesting

# For notifications
pip3 install python-telegram-bot

# Install any other libraries your bot uses

### 3.4 Install Screen (for running bot persistently)

In [ ]:
sudo apt install screen -y

## Step 4: Upload Your Bot Code

### 4.1 Method 1: Using SCP (Secure Copy) - Linux/Mac

In [ ]:
# From your local machine, copy your bot files (run in local terminal):
scp -r /path/to/your/bot/folder root@YOUR_SERVER_IP:/root/trading-bot/

# Example:
scp -r ~/Desktop/my-crypto-bot root@YOUR_SERVER_IP:/root/trading-bot/

### 4.2 Method 1: Using SCP - Windows

In [ ]:
# In Windows Terminal or PowerShell (run locally):
scp -r C:\path\to\your\bot\folder root@YOUR_SERVER_IP:/root/trading-bot/

# Example:
scp -r C:\Users\YourName\Desktop\my-crypto-bot root@YOUR_SERVER_IP:/root/trading-bot/

### 4.3 Method 2: Using Git (Recommended)

In [ ]:
# On your server:
cd /root/
git clone https://github.com/yourusername/your-trading-bot.git
cd your-trading-bot

# Or if you don't have git repo, create directory and use nano:
mkdir trading-bot
cd trading-bot
nano main.py
# Paste your code, save with Ctrl+X, Y, Enter

### 4.4 Method 3: Using File Transfer (Windows PuTTY users)
1. Download WinSCP from [winscp.net](https://winscp.net/)
2. Connect using same credentials as PuTTY
3. Drag and drop your bot files to `/root/trading-bot/`

## Step 5: Configure Environment Variables

### What are .env files?

**Environment Variables & .env Files Explained**

**What is a .env file?**
- A simple text file that stores configuration data
- Contains key-value pairs (API_KEY=your_secret_key)
- Kept separate from your main code

**Why use .env files?**
- **Security**: Keeps secrets out of your code
- **Flexibility**: Easy to change settings without editing code
- **Version Control**: Never accidentally commit API keys to GitHub
- **Environment-specific**: Different keys for testing vs production

### 5.1 Create .env File

In [ ]:
cd /root/trading-bot
nano .env

### 5.2 Add Your API Keys

In the nano editor, add your keys:

In [ ]:
# Example .env file content:
BINANCE_API_KEY=your_actual_api_key_here
BINANCE_SECRET=your_actual_secret_key_here

# Save: Ctrl+X, then Y, then Enter

### 5.3 Using .env in Your Python Code

In [ ]:
import os
from dotenv import load_dotenv

# Load environment variables
load_dotenv()

# Access your API keys
api_key = os.getenv('BINANCE_API_KEY')
secret_key = os.getenv('BINANCE_SECRET')

print(f"API Key loaded: {api_key[:10]}...")

### 5.4 Secure Your .env File

In [ ]:
# Make file readable only by owner
chmod 600 .env

# Verify permissions
ls -la .env
# Should show: -rw------- 1 root root

## Step 6: Test Your Bot

### 6.1 Run a Test

In [ ]:
cd /root/trading-bot
python3 main.py

### 6.2 Run in Background with Screen

In [ ]:
# Create a new screen session
screen -S trading-bot

# Run your bot
python3 main.py

# Detach from screen: Ctrl+A, then D
# Reattach later: screen -r trading-bot
# List screens: screen -ls

## Step 7: Set Up Automatic Restart (Optional)

### 7.1 Create a Systemd Service

In [ ]:
sudo nano /etc/systemd/system/trading-bot.service

### 7.2 Add Service Configuration

Add this content to the service file:

In [ ]:
[Unit]
Description=Crypto Trading Bot
After=network.target

[Service]
Type=simple
User=root
WorkingDirectory=/root/trading-bot
ExecStart=/usr/bin/python3 /root/trading-bot/main.py
Restart=always
RestartSec=10

[Install]
WantedBy=multi-user.target

### 7.3 Enable and Start Service

In [ ]:
# Reload systemd
sudo systemctl daemon-reload

# Enable service (start on boot)
sudo systemctl enable trading-bot

# Start service now
sudo systemctl start trading-bot

# Check status
sudo systemctl status trading-bot

# View logs
sudo journalctl -u trading-bot -f

## Common Commands Reference

### Server Management

In [ ]:
# Check running processes
ps aux | grep python

# Kill a process
kill PID_NUMBER

# Check system resources
htop
# (install with: sudo apt install htop)

# Check disk space
df -h

# Check memory usage
free -h

### Screen Commands

In [ ]:
# Create new screen
screen -S session_name

# List screens
screen -ls

# Reattach to screen
screen -r session_name

# Detach from screen
# Ctrl+A, then D

# Kill screen session
screen -X -S session_name quit

### File Operations

In [ ]:
# View file contents
cat filename.py

# Edit file
nano filename.py

# Copy file
cp source.py backup.py

# Move/rename file
mv oldname.py newname.py

# Delete file
rm filename.py

## Troubleshooting

### Connection Issues
- **Can't connect via SSH**: Check if server is running in Hetzner console
- **Permission denied**: Make sure you're using correct username (root) and IP
- **SSH key issues**: Try password authentication first

### Python Issues
- **ModuleNotFoundError**: Install missing packages with `pip3 install package_name`
- **Permission errors**: Make sure you're in the correct directory
- **Python version issues**: Use `python3` instead of `python`

### Bot Issues
- **API errors**: Double-check your .env file and API key permissions
- **Network errors**: Check internet connection with `ping google.com`
- **Log errors**: Check bot output for specific error messages

### Getting Help

In [ ]:
# Check system logs
sudo journalctl -xe

# Check your bot logs if using systemd
sudo journalctl -u trading-bot -f

# Monitor system resources
htop

## 🎉 Congratulations!

**Your trading bot is now running on Hetzner Cloud!**

**Next Steps:**
- Monitor your bot's performance
- Set up alerts/notifications
- Consider adding more sophisticated error handling
- Scale up server resources if needed

**Remember:**
- Start with small position sizes
- Test thoroughly before going live
- Always have kill switches ready
- Monitor your bot regularly